Import required packages

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.metrics.pairwise import linear_kernel
from copy import deepcopy
from scipy.spatial.distance import pdist, squareform
from scipy.sparse import csr_matrix
from sklearn.neighbors import NearestNeighbors
from fuzzywuzzy import process
from sklearn.metrics import mean_squared_error, mean_absolute_error

Read the file

In [2]:
file = pd.read_excel('shortcourses2566.xlsx')

Count the number of courses

In [3]:
course_counts = pd.DataFrame(file)['หลักสูตรอบรมระยะสั้น'].value_counts()
courses = pd.Series(course_counts.index)
courses = courses.sort_values().set_axis(range(0,len(courses)))

Create Series of users

In [4]:
s_name = file.loc[:, 'ชื่อ-นามสกุล (อังกฤษ)']
Users = pd.Series(s_name, name='User')
Users

0             PORPHAING JANTIP
1         THANAKORN DARASRISAK
2             KARNJANA EAMTANG
3             KARNJANA EAMTANG
4       THITIMUN VORATHONGCHAI
                 ...          
6122         KITTINON SANTASUP
6123      WITTAWAT SERMSRIPONG
6124               NON NAKKARA
6125         PHATTHARAPHON LIN
6126      THANAPAT SEEMAKAJOHN
Name: User, Length: 6127, dtype: object

Create Series of emails

In [5]:
s_email = file.loc[:, 'อีเมล'].fillna("")
Emails = pd.Series(s_email ,name='Email')
Emails

0            tanghaoren17@gamil.com
1               tuakung21@gmail.com
2            karnjana.aon@gmail.com
3            karnjana.aon@gmail.com
4          thitimun.rama1@gmail.com
                   ...             
6122           kittinon_s@cmu.ac.th
6123        wittawat_serm@cmu.ac.th
6124          non_nakkara@cmu.ac.th
6125    phattharaphon_lin@cmu.ac.th
6126         thanapat_see@cmu.ac.th
Name: Email, Length: 6127, dtype: object

Provide a score to each user based on their email domain

In [6]:
email_score = []
for data in Emails:
    if data != '':
        if data.split('@')[1] == 'cmu.ac.th':
            email_score.append(2)
        else:
            email_score.append(1)
    else:
        email_score.append(0)
email_score = pd.Series(email_score, name='Score Email')

email_score

0       1
1       1
2       1
3       1
4       1
       ..
6122    2
6123    2
6124    2
6125    2
6126    2
Name: Score Email, Length: 6127, dtype: int64

Email Score Statistic

In [7]:
zero_score_count = email_score.where(email_score == 0).count()
one_score_count = email_score.where(email_score == 1).count()
two_score_count = email_score.where(email_score == 2).count()

print("Number of students who filled cmu email:", two_score_count)
print("Number of students who filled other email:", one_score_count)
print("Number of students who did not fill email:", zero_score_count)

Number of students who filled cmu email: 1268
Number of students who filled other email: 4853
Number of students who did not fill email: 6


Create function to calculate age-education score

In [8]:
def getAgeEducationScore(age, limit_age):
    if age <= limit_age:
        score = 0
    elif age <= limit_age + 2:
        score = 1
    else:
        score = 2
    return score

Create set of the educational range

In [9]:
set_nan = {'อื่นๆ (-)', np.nan}
set_primaryschool = {'ประถมศึกษา', 'อื่นๆ (ป.4)', 'อื่นๆ (ป.7)', 'อื่นๆ (ป7)'}
set_middleschool = {'มัธยมศึกษาตอนต้น', 'Secondary school', 'อื่นๆ (มศ.3)'}
set_highschool = {'มัธยมศึกษาตอนปลาย', 'High school', 'Vocational', 'การศึกษานอกระบบ', 
                  'ประกาศนียบัตรวิชาชีพ (ปวช.)', 'อื่นๆ (ม.ปลาย จบหลักสูตรEMR เป็นจนท.ปฏิบัติการ)',
                  'อื่นๆ (กำลังศึกษาชั้นมัธยมศึกษาตอนปลาย)', 'อื่นๆ (กำลังศึกษาชั้นมัธยมศึกษาปีที่6)', 
                  'อื่นๆ (มศ.5)'}
set_bachelor = {'ปริญญาตรี', 'Bachelor degree', 'Diploma', 'High Vocational', 
                'ประกาศนียบัตรวิชาชีพชั้นสูง (ปวส.)', 'อื่นๆ (กำลังศึกษาในระดับปริญญาตรี)', 
                'อื่นๆ (กำลังศึกษาปริญญาตรี สาขารังสีเทคนิค)', 'อื่นๆ (ปริญญาแพทยศาสตร์บัณฑิต)', 
                'อื่นๆ (นักศึกษาแพทย์ปี 5)', 'อื่นๆ (นักศึกษาแพทย์ มช ปี4 ศูนย์เชียงราย)', 
                'อื่นๆ (แพทยศาสตร์บัณฑิต)', 'อื่นๆ (แพทย์)', 'อื่นๆ (ประกาศณียบัตรผู้ช่วยพยาบาล)', 
                'อนุปริญญา', 'อื่นๆ (ป.ตรี)', 'อื่นๆ (ผู้ช่วยพยาบาล)'}
set_masterdocter = {'ปริญญาโท', 'ปริญญาเอก', "Master's degree", 'Other (OBGYN specalist lavel 1)', 
                    'Other (Residency)', 'Ph.D.', 'อื่นๆ (Internal Medicine)', 
                    'อื่นๆ (เฉพาะทาง)', 'อื่นๆ (วุฒิบัตร)', 'อื่นๆ (วว.ออร์โธปิดิกส์)', 
                    'อื่นๆ (วุฒิบัตรแสดงความรู้ความชำนาญในการประกอบวิชาชีพเภสัชกรรม สาขาเภสัชบำบัด)', 
                    'อื่นๆ (วุฒิบัตรผู้เชี่ยวชาญสาขาทันตกรรมทั่วไป)', 'อื่นๆ (วุฒิบัตรศัลยศาสตร์และแม็กซิลโลเฟเชียล)'}

list_degree = ((set_nan, 0), (set_primaryschool, 16), (set_middleschool, 19), 
               (set_highschool, 22), (set_bachelor,26), (set_masterdocter,40))

Create Series of Age-Education

In [10]:
ages = file.loc[:, 'อายุ']
educations = file.loc[:, 'วุฒิการศึกษา']
age_education_scores = []

for i,x in enumerate(educations):
    for y in list_degree:
        if x in y[0]:
            age_education_scores.append(getAgeEducationScore(ages[i], y[1]))
            
age_education_scores = pd.Series(age_education_scores, name='Age Education Score')

Age-Education Score Statistic

In [11]:
zero_score_count = age_education_scores.where(age_education_scores == 0).count()
one_score_count = age_education_scores.where(age_education_scores == 1).count()
two_score_count = age_education_scores.where(age_education_scores == 2).count()

print("Number of students who are currently in the educational system:", zero_score_count)
print("Number of students who were recently graduated:", one_score_count)
print("Number of students who are not in the educational system:", two_score_count)

Number of students who are currently in the educational system: 4229
Number of students who were recently graduated: 487
Number of students who are not in the educational system: 1411


Create Series of status

In [12]:
status = file.loc[:, 'สถานะ'].fillna("")
status = pd.Series(status ,name='Status')
status

0       ชำระเงิน
1       ชำระเงิน
2       ชำระเงิน
3       ชำระเงิน
4       ชำระเงิน
          ...   
6122    ชำระเงิน
6123    ชำระเงิน
6124    ชำระเงิน
6125    ชำระเงิน
6126    ชำระเงิน
Name: Status, Length: 6127, dtype: object

Provide a score to each user based on their purchase status

In [13]:
status_score = []
for x in status:
    if x == 'ชำระเงิน':
        status_score.append(2)
    if x == 'ไม่ผ่านการอนุมัติ':
        status_score.append(1)
    if x == 'ค้างชำระ':
        status_score.append(0)
status_score = pd.Series(status_score)

Purchase Status Score Statistics

In [14]:
zero_score_count = status_score.where(status_score == 0).count()
one_score_count = status_score.where(status_score == 1).count()
two_score_count = status_score.where(status_score == 2).count()

print("Number of students who are in arrears:", zero_score_count)
print("Number of students whose payment was not approved:", one_score_count)
print("Number of students with payment approval:", two_score_count)

Number of students who are in arrears: 531
Number of students whose payment was not approved: 124
Number of students with payment approval: 5472


Create Series of address

In [15]:
address = file.loc[:, 'ที่อยู่'].fillna("")
address = pd.Series(address ,name='Status')
address

0                                                        
1       125/27 ซ.3 ถ.ราษฎรยินดี ต.หน้าเมือง อ.เมือง จ....
2                                                        
3                                                        
4                                                        
                              ...                        
6122                                                     
6123                                                     
6124                                                     
6125                                                     
6126                                                     
Name: Status, Length: 6127, dtype: object

Provide a score to each user based on whether they provide address information or not

In [16]:
address_score = [ 0 if x == '' else 1 for x in address]
address_score = pd.Series(address_score)

Address Score Statistic

In [17]:
zero_score_count = address_score.where(address_score == 0).count()
one_score_count = address_score.where(address_score == 1).count()

print("Number of students who did not fill address:", zero_score_count)
print("Number of students who filled address:", one_score_count)

Number of students who did not fill address: 4005
Number of students who filled address: 2122


Create Series of data

In [18]:
enrollment = file.loc[:, 'วันที่สมัครอบรม'].fillna("")
enrollment = pd.Series(enrollment ,name='Date')
enrollment = enrollment.str.slice(start=-8, stop=-6)

Provide a score to each user based on their enrollment time

In [19]:
enrollment_set = {'08','09','10','15'}
enrollment_score = [ 1 if x in enrollment_set else 0 for x in enrollment]
enrollment_score = pd.Series(enrollment_score)

Create DataFrame by merging these 4 Series and calculate impressive level

In [49]:
user = file.loc[:, 'ชื่อ-นามสกุล (อังกฤษ)']
course = file.loc[:, 'หลักสูตรอบรมระยะสั้น']
d = {
    'User': user,
    'Course': course,
    'Email Score': email_score,
    'Age Education Score': age_education_scores,
    'Enrollment': enrollment_score,
    'Payment Score': status_score,
    'Address Score': address_score,
    'Score': 1 + email_score*0.75 + status_score*1 + address_score*0.25 + age_education_scores*0.25 + enrollment_score*0.5 
}
df = pd.DataFrame(d)
pd.set_option('display.max_rows', df.shape[0]+1)
df

User  \
0                                      PORPHAING JANTIP   
1                                  THANAKORN DARASRISAK   
2                                      KARNJANA EAMTANG   
3                                      KARNJANA EAMTANG   
4                                THITIMUN VORATHONGCHAI   
5                              PEERACHET POOSUNTISOMPUN   
6                                    WARACHAN CHAIKANTA   
7                                    WARACHAN CHAIKANTA   
8                                  WARIT DENSRISEREEKUL   
9                                     NARINTIPP SHUSANG   
10                                    NARINTIPP SHUSANG   
11                                  NUSSAREEYA CHOBNGAM   
12                                  NUSSAREEYA CHOBNGAM   
13                                      AMPORN MALISORN   
14                                     SUNANTHA THINRAJ   
15                                   APISARA PHAOWTAJAI   
16                                PUKKAPOL SUVANNACHART   
17                                            TING ZHOU   
18                                WARUNYAPORN PHROMPHAT   
19                                THANUNCHANOK KOMGRONG   
20                               PUNLOP SOONTHONCHAROEN   
21                                  BENJAMAT ANTHAPANYA   
22                              Ms. NATTAPHAN SIRITIKUL   
23                                    ATSAKORN MOTSAENG   
24                                WIRINYA SAENGTHAMCHAI   
25                                     JACK VORAPHAKDEE   
26                             Ms. PATCHARAPORN KAEWTIN   
27                                Mr. KALUNYU KOTCHAWAT   
28                                    ATSAKORN MOTSAENG   
29                                    ATSAKORN MOTSAENG   
30                              Ms. TAMONWAN CHOOMCHEUN   
31                                     SITTICHAI ONGTIP   
32                                      SORAWIT PROMRAK   
33                           Miss SASATORN THONGBUAKAEO   
34                                     SARANYA INTHAPAD   
35                                 THANAWAN PONGPRUEKSA   
36                                         ANAN CHOMKUM   
37                                PATTHARAWIPA SONGYANG   
38                                   KRITTEE CHESDACHAI   
39                               KANOKKAN DUANGSUWANKUL   
40                           SUDARAT JARUWATTANACHAIKUL   
41                                Ms. APINYAPORN KITKOM   
42                                    SAWANRAT PANYAWAI   
43                                JITRAPORN SUVARANARAK   
44                                 CHANUNCHIDA PHUAKNOI   
45                                         METAS PETHAN   
46                            Mr. CHAYANGKOON NOLAKMUEN   
47                        Mr. PURINUT WATTANAWONGVIBOON   
48                          PATCHARAPORN PITAKCHARTWONG   
49                               Mr. TAKKASART FOYTHONG   
50                                     WATCHARAPONG NON   
51                                Mr. METUS OUNTAVEESAP   
52                                   SUPAMART SUESAMRIT   
53                              ANCHITHA PEERAPORNVIMOL   
54                                  Ms. KANJANA TEPAKAM   
55                             Mr. WITTHAWAT PRUTKACHAT   
56                                PHOT PHAIBOONWORACHAT   
57                                PHOT PHAIBOONWORACHAT   
58                                         ANAN CHOMKUM   
59                              Ms. SATREERAT KAEWYUANG   
60                                 Ms. CHALIDA JAIMANEE   
61                                  Ms. NARITSARA OONAT   
62                           Mr. KHEUNPETCH JANTARAMANO   
63                                 Mr. ANUPANG PONGSUPA   
64                                 Miss MATTHANA PAOPAT   
65                              Miss WANNAPA RATTIKANOK   
66                                Miss TAMONWAN KARATON   
67                     Mr. WAYUPAK WATC

Create user-course table

In [50]:
# all user, course, score have the same length
data = {
    'User': df['User'],
    'Course': df['Course'],
    'Score': df['Score'],
}

predata = pd.DataFrame(data)
predata

User  \
0                                      PORPHAING JANTIP   
1                                  THANAKORN DARASRISAK   
2                                      KARNJANA EAMTANG   
3                                      KARNJANA EAMTANG   
4                                THITIMUN VORATHONGCHAI   
5                              PEERACHET POOSUNTISOMPUN   
6                                    WARACHAN CHAIKANTA   
7                                    WARACHAN CHAIKANTA   
8                                  WARIT DENSRISEREEKUL   
9                                     NARINTIPP SHUSANG   
10                                    NARINTIPP SHUSANG   
11                                  NUSSAREEYA CHOBNGAM   
12                                  NUSSAREEYA CHOBNGAM   
13                                      AMPORN MALISORN   
14                                     SUNANTHA THINRAJ   
15                                   APISARA PHAOWTAJAI   
16                                PUKKAPOL SUVANNACHART   
17                                            TING ZHOU   
18                                WARUNYAPORN PHROMPHAT   
19                                THANUNCHANOK KOMGRONG   
20                               PUNLOP SOONTHONCHAROEN   
21                                  BENJAMAT ANTHAPANYA   
22                              Ms. NATTAPHAN SIRITIKUL   
23                                    ATSAKORN MOTSAENG   
24                                WIRINYA SAENGTHAMCHAI   
25                                     JACK VORAPHAKDEE   
26                             Ms. PATCHARAPORN KAEWTIN   
27                                Mr. KALUNYU KOTCHAWAT   
28                                    ATSAKORN MOTSAENG   
29                                    ATSAKORN MOTSAENG   
30                              Ms. TAMONWAN CHOOMCHEUN   
31                                     SITTICHAI ONGTIP   
32                                      SORAWIT PROMRAK   
33                           Miss SASATORN THONGBUAKAEO   
34                                     SARANYA INTHAPAD   
35                                 THANAWAN PONGPRUEKSA   
36                                         ANAN CHOMKUM   
37                                PATTHARAWIPA SONGYANG   
38                                   KRITTEE CHESDACHAI   
39                               KANOKKAN DUANGSUWANKUL   
40                           SUDARAT JARUWATTANACHAIKUL   
41                                Ms. APINYAPORN KITKOM   
42                                    SAWANRAT PANYAWAI   
43                                JITRAPORN SUVARANARAK   
44                                 CHANUNCHIDA PHUAKNOI   
45                                         METAS PETHAN   
46                            Mr. CHAYANGKOON NOLAKMUEN   
47                        Mr. PURINUT WATTANAWONGVIBOON   
48                          PATCHARAPORN PITAKCHARTWONG   
49                               Mr. TAKKASART FOYTHONG   
50                                     WATCHARAPONG NON   
51                                Mr. METUS OUNTAVEESAP   
52                                   SUPAMART SUESAMRIT   
53                              ANCHITHA PEERAPORNVIMOL   
54                                  Ms. KANJANA TEPAKAM   
55                             Mr. WITTHAWAT PRUTKACHAT   
56                                PHOT PHAIBOONWORACHAT   
57                                PHOT PHAIBOONWORACHAT   
58                                         ANAN CHOMKUM   
59                              Ms. SATREERAT KAEWYUANG   
60                                 Ms. CHALIDA JAIMANEE   
61                                  Ms. NARITSARA OONAT   
62                           Mr. KHEUNPETCH JANTARAMANO   
63                                 Mr. ANUPANG PONGSUPA   
64                                 Miss MATTHANA PAOPAT   
65                              Miss WANNAPA RATTIKANOK   
66                                Miss TAMONWAN KARATON   
67                     Mr. WAYUPAK WATC

Calculate sparsity and csr matrix

In [51]:
# Pivot table by rotating course
data = pd.pivot_table(predata, values='Score', index='Course', columns='User').fillna(0)
data

User                                                AAIYANA MUSTAFA  \
Course                                                                
Cancer Epidemiology and Prevention                             0.00   
Coaching Skill : Crafting a New You สำหรับนักศึ...             0.00   
Coaching Skill : Crafting a New You สำหรับบุคลา...             0.00   
Development Studies & Social Research Specializ...             0.00   
Digital Transformation: e-Document                             0.00   
Environmental Economics (USAC programs) - Fall ...             0.00   
Global Citizenship – โรงเรียนมงฟอร์ตวิทยาลัย สำ...             0.00   
Global Citizenship – โรงเรียนมงฟอร์ตวิทยาลัย สำ...             0.00   
Global Citizenship – โรงเรียนสันป่าตองวิทยาคม 2566             0.00   
Global Citizenship – โรงเรียนแม่ริมวิทยาคม 2566                0.00   
Global Politics – โรงเรียนปรินส์รอยแยลส์วิทยาลั...             0.00   
Global Politics – โรงเรียนสันป่าตองวิทยาคม 2566                0.00   
Global Politics – โรงเรียนแม่ริมวิทยาคม 2566                   0.00   
Mindfulness for Life and Learning : สติเพื่อชีว...             0.00   
Mindfulness for Life and Work : สติเพื่อชีวิตแล...             0.00   
Modern Chinese History (USAC program) – Spring ...             0.00   
Political Science and Public Administration for...             0.00   
Political Science and Public Administration for...             0.00   
Sociology and Anthropology of Northern Thailand...             0.00   
Sociology and Anthropology of Northern Thailand...             0.00   
Sustainable Agriculture Development (USAC progr...             0.00   
Sustainable Agriculture Development (USAC progr...             0.00   
Thai Cultural Education for International Stude...             0.00   
Thai Cultural Education for International Stude...             0.00   
Thai Cultural Education for International Stude...             0.00   
Thai Cultural Education for International Stude...             0.00   
World Economic Issues (USAC program) – Spring S...             0.00   
World Economic Issues (USAC program) – Summer 2...             0.00   
กฎหมายกีฬาเบื้องต้น (Introduction to Sports Law)               0.00   
การขับร้องประสานเสียงขั้นพื้นฐาน                               0.00   
การชันสูตรศพและการสอนการชันสูตรศพตามกฎหมาย (Dip...             0.00   
การดูแลสุขภาพสำหรับสัตว์เลี้ยง (Health Care of ...             0.00   
การตรวจวิเคราะห์พื้นฐานทางพิษวิทยาและการตรวจวิเ...             0.00   
การบริบาลทางเภสัชกรรม สาขาผู้ป่วยมะเร็ง (ปี 256...             0.00   
การบริบาลทางเภสัชกรรม สาขาอายุรศาสตร์ (ปี 2567)...             0.00   
การบริบาลทางเภสัชกรรมในผู้ป่วยโรคหัวใจและหลอดเล...             0.00   
การบริบาลทางเภสัชกรรมในผู้ป่วยโรคหัวใจและหลอดเล...             0.00   
การป้องกันการล้มสำหรับผู้สูงอายุ                               0.00   
การฝึกอบรมเนื้อหาดิจิทัล (Digital Content) ประจ...             0.00   
การพัฒนาปัญญาด้วยเกมต่อศัพท์ภาษาอังกฤษ (Intelle...             0.00   
การวิจัยด้านวิศวกรรมชีวการแพทย์ (Research in Bi...             0.00   
การวิจัยแบบผสมผสานทางสุขภาพ (Mixed Methods Rese...             0.00   
การวินิจฉัยภาวะฉุกเฉินจากอุบัติเหตุ (Diagnostic...             0.00   
การวินิจฉัยภาวะฉุกเฉินที่ไม่ได้เกิดจากอุบัติเหต...             0.00   
การวิเคราะห์ข้อมูลการวิจัยทางพฤติกรรมศาสตร์และส...             0.00   
การวิเคราะห์ข้อมูลขนาดใหญ่ทางสาธารณสุข (Big Dat...             0.00   
การวิเคราะห์ข้อมูลอัจฉริยะด้วย RapidMiner (Inte...             0.00   
การวิเคราะห์ผลตอบแทนทางสังคมในงานด้านสุขภาพ (So...             0.00   
การสร้าง AI ขั้นพื้นฐานด้วย RapidMiner และ Exce...             0.00   
การสอบวัดผลการเรียนรู้ระดับมัธยมปลาย (ม.6) สำหร...             0.00   
การออกแบบกิจกรรมผ่านจิตวิทยาเชิงบวก รุ่นที่ 1                  0.00   
การออกแบบกิจกรรมผ่านจิตวิทยาเชิงบวก รุ่นที่ 2                  0.00   
การอำนวยเพลงและการสอนวงขับร้องประสานเสียง                      0.00   
การเขียนแบบวิศวกรรม (Engineering Drawing) - สำห...             0.00   
การเขียนแบบวิศวกรรม (Eng

In [52]:
# Item-User Rated Matrix
data_mtx = csr_matrix(data.values)

Euclidean Distance & Cosine Similarity

In [53]:
model_knn = NearestNeighbors(metric='cosine', algorithm='brute').fit(data_mtx)
model_knn

NearestNeighbors(algorithm='brute', metric='cosine')

In [55]:
def recommender_knn(course_name, n_recommendations):
    idx = process.extractOne(course_name, courses)[2]
    print('Selected movie:', courses[idx], 'Index:', idx)
    distances, indices = model_knn.kneighbors(data_mtx[idx], n_neighbors=n_recommendations+1, return_distance=True)
    recommendations = [courses[i].where(i!=idx) for i in indices]
    recommended_courses = recommendations[0][1:]
    course_distances = distances[0][1:]
    d = {
        'Course': recommended_courses,
        'Cosine Distance': course_distances
    }
    results = pd.DataFrame(data=d)
    return results

In [56]:
recommender_knn('หลักการและพื้นฐานของเครื่องมือทางรังสีวิทยา (Basic Principle of Diagnostic Radiology Imaging Instruments)', 167)

Selected movie: หลักการและพื้นฐานของเครื่องมือทางรังสีวิทยา (Basic Principle of Diagnostic Radiology Imaging Instruments) Index: 131


Course  Cosine Distance
152  เตรียมความพร้อมทางรังสีวิทยาสำหรับบุคลากรทางกา...         0.675067
42   การวินิจฉัยภาวะฉุกเฉินจากอุบัติเหตุ (Diagnosti...         0.722855
43   การวินิจฉัยภาวะฉุกเฉินที่ไม่ได้เกิดจากอุบัติเห...         0.755242
163                           เวชศาสตร์ครอบครัวขั้นสูง         0.940557
85   ความรู้พื้นฐานในการทำวิจัยเพื่อพัฒนางาน (Resea...         0.973442
110                                 รังสีวิทยาวินิจฉัย         0.975044
105  บทนำสู่รังสีเทคนิค (Introduction to Radiologic...         0.975584
59   การเขียนโครงการและกระบวนการใช้จ่ายเงินในกิจกรร...         0.976519
136  หลักสูตรอบรมเข้มข้นระยะสั้นแพทย์-วิศวกรรมและวิ...         0.977016
117  วิทยาศาสตร์การแพทย์คลินิก สาขาวิชาเวชศาสตร์ฉุก...         0.978279
90   จิตเวชศาสตร์สำหรับแพทย์เวชปฏิบัติ (Psychiatry ...         0.980491
148  เตรียมความพร้อมด้านดิจิทัลและทักษะภาษาอังกฤษ ส...         0.982791
133  หลักสูตรย่อยที่ 1 พื้นฐานการดูแลสุขภาพสัตว์เลี...         0.983154
106            บทนำสู่วิชาชีพกายภาพบำบัด รุ่น 2 (2566)         0.983543
119  วิธีวิทยาการวิจัยทางการศึกษา (Research Methodo...         0.984130
100  นักวางแผนข้อมูลเมือง (City Data Planner : CDP)...         0.984985
121  สถิติศาสตร์คลินิก 2566 (Diploma in Clinical St...         0.985646
123  สอบคัดเลือกเพื่อเข้าอบรมหลักสูตรอบรมเข้มข้นระย...         0.986535
3    Development Studies & Social Research Speciali...         0.986898
162  เรียนรู้การคิดเชิงออกแบบ (Design Thinking) : ท...         0.987775
41   การวิจัยแบบผสมผสานทางสุขภาพ (Mixed Methods Res...         0.988596
7    Global Citizenship – โรงเรียนมงฟอร์ตวิทยาลัย ส...         0.992046
51       การออกแบบกิจกรรมผ่านจิตวิทยาเชิงบวก รุ่นที่ 2         0.992094
165  แปลงจุดแข็ง เป็นคุณค่า สร้างชีวิตสู่ความสุข  (...         0.992513
94   ถอดรหัสอารมณ์เพื่อการเข้าใจตนเอง (Understandin...         0.992625
71   การเตรียมความพร้อมในการคุ้มครองข้อมูลส่วนบุคคล...         0.992770
29                    การขับร้องประสานเสียงขั้นพื้นฐาน         0.993673
161  เรียนรู้การคิดเชิงออกแบบ (Design Thinking) : ท...         0.993896
167  “ฟูมฟักทักษะสำคัญในชีวิตและการทำงาน Skills4Lif...         0.995387
31   การดูแลสุขภาพสำหรับสัตว์เลี้ยง (Health Care of...         0.996519
99   นักพัฒนาหัตถกรรมอัจฉริยะ (Smart Craft) ที่เชื่...         0.996730
84   ความรู้พื้นฐานด้านอาชีวเวชศาสตร์สำหรับแพทย์ (F...         0.996746
55   การเขียนแบบวิศวกรรม (Engineering Drawing) 2566...         0.997341
109  ระเบียบวิธีวิจัยทางสาธารณสุข (Research Methodo...         1.000000
97                            ทดสอบการชำระเงิน Qr code         1.000000
96                        ทดสอบการชำระเงิน Credit card         1.000000
101  นักศึกษาโครงการ University Studies Abroad Cons...         1.000000
118  วิทยาศาสตร์ขั้นสูงในการดูแลผิวพรรณและสุขภาวะผิ...         1.000000
92   ซัมเมอร์บูทแคมป์ แคลคูลัส พิชิตฝัน (Math Sci C...         1.000000
102  นักศึกษาโครงการ University Studies Abroad Cons...         1.000000
116  วิทยาศาสตร์การแพทย์คลินิก สาขาวิชารังสีรักษาแล...         1.000000
115       วิทยาศาสตร์การแพทย์คลินิก สาขาวิชาพยาธิวิทยา         1.000000
104         นิติเวชคลินิก (Clinical Forensic Medicine)         1.000000
108  ผลิตภัณฑ์สลีปปิ้งมาสก์สำหรับผิวหน้าจากสารสกัดข...         1.000000
95   ถอดรหัสอารมณ์เพื่อการเข้าใจตนเอง (Understandin...         1.000000
114       วิทยาศาสตร์การแพทย์คลินิก สาขาวิชาจักษุวิทยา         1.000000
113   วิทยาศาสตร์การแพทย์คลินิก สาขาวิชากุมารเวชศาสตร์         1.000000
93   ต้นแบบ (Figma) สู่การ Front End Dev (Tailwind ...         1.000000
112  วัสดุวิศวกรรม (Engineering Materials) 2566 - ร...         1.000000
98                               ทักษะความเป็นนักดนตรี         1.000000
107  ประสาทวิทยาคลินิกทางสัตวแพทย์ (Veterinary Clin...         1.000000
103  นักออกแบบนวัตกรรมชุมชน รุ่นที่ 5 (Community In...         1.000000
111  วัสดุวิศวกรรม (Engineering Materials) 2566 - ร...         1.000000
0                   Cancer Epidemiology and Prevention         1.000000
122  สถิติศาสตร์คลินิก 2566 (Diploma in Clinical St...         1.000000
146  เตรียมความพ

Predata for hybrid recommendation

In [57]:
def recommender_knn_all_courses(course_name):
    model_knn.fit(data_mtx)
    idx = process.extractOne(course_name, courses)[2]
    # print('Selected movie:', courses[idx], 'Index:', idx)
    distances, indices = model_knn.kneighbors(data_mtx[idx], n_neighbors=len(courses))
    recommendations = [courses[i].where(i!=idx) for i in indices]
    recommended_courses = recommendations[0][1:]
    scores = 1 - distances
    course_distances = scores[0][1:]
    d = {
        'Course': recommended_courses,
        'Score': course_distances
    }
    results = pd.DataFrame(data=d)
    results = results.sort_index().rename_axis('Index')
    return results

In [58]:
recommender_knn_all_courses('หลักการและพื้นฐานของเครื่องมือทางรังสีวิทยา (Basic Principle of Diagnostic Radiology Imaging Instruments)')

Course     Score
Index                                                             
0                     Cancer Epidemiology and Prevention  0.000000
1      Coaching Skill : Crafting a New You สำหรับนักศ...  0.000000
2      Coaching Skill : Crafting a New You สำหรับบุคล...  0.000000
3      Development Studies & Social Research Speciali...  0.013102
4                     Digital Transformation: e-Document  0.000000
5      Environmental Economics (USAC programs) - Fall...  0.000000
6      Global Citizenship – โรงเรียนมงฟอร์ตวิทยาลัย ส...  0.000000
7      Global Citizenship – โรงเรียนมงฟอร์ตวิทยาลัย ส...  0.007954
8      Global Citizenship – โรงเรียนสันป่าตองวิทยาคม ...  0.000000
9        Global Citizenship – โรงเรียนแม่ริมวิทยาคม 2566  0.000000
10     Global Politics – โรงเรียนปรินส์รอยแยลส์วิทยาล...  0.000000
11       Global Politics – โรงเรียนสันป่าตองวิทยาคม 2566  0.000000
12          Global Politics – โรงเรียนแม่ริมวิทยาคม 2566  0.000000
13     Mindfulness for Life and Learning : สติเพื่อชี...  0.000000
14     Mindfulness for Life and Work : สติเพื่อชีวิตแ...  0.000000
15     Modern Chinese History (USAC program) – Spring...  0.000000
16     Political Science and Public Administration fo...  0.000000
17     Political Science and Public Administration fo...  0.000000
18     Sociology and Anthropology of Northern Thailan...  0.000000
19     Sociology and Anthropology of Northern Thailan...  0.000000
20     Sustainable Agriculture Development (USAC prog...  0.000000
21     Sustainable Agriculture Development (USAC prog...  0.000000
22     Thai Cultural Education for International Stud...  0.000000
23     Thai Cultural Education for International Stud...  0.000000
24     Thai Cultural Education for International Stud...  0.000000
25     Thai Cultural Education for International Stud...  0.000000
26     World Economic Issues (USAC program) – Spring ...  0.000000
27     World Economic Issues (USAC program) – Summer ...  0.000000
28      กฎหมายกีฬาเบื้องต้น (Introduction to Sports Law)  0.000000
29                      การขับร้องประสานเสียงขั้นพื้นฐาน  0.006327
30     การชันสูตรศพและการสอนการชันสูตรศพตามกฎหมาย (Di...  0.000000
31     การดูแลสุขภาพสำหรับสัตว์เลี้ยง (Health Care of...  0.003481
32     การตรวจวิเคราะห์พื้นฐานทางพิษวิทยาและการตรวจวิ...  0.000000
33     การบริบาลทางเภสัชกรรม สาขาผู้ป่วยมะเร็ง (ปี 25...  0.000000
34     การบริบาลทางเภสัชกรรม สาขาอายุรศาสตร์ (ปี 2567...  0.000000
35     การบริบาลทางเภสัชกรรมในผู้ป่วยโรคหัวใจและหลอดเ...  0.000000
36     การบริบาลทางเภสัชกรรมในผู้ป่วยโรคหัวใจและหลอดเ...  0.000000
37                      การป้องกันการล้มสำหรับผู้สูงอายุ  0.000000
38     การฝึกอบรมเนื้อหาดิจิทัล (Digital Content) ประ...  0.000000
39     การพัฒนาปัญญาด้วยเกมต่อศัพท์ภาษาอังกฤษ (Intell...  0.000000
40     การวิจัยด้านวิศวกรรมชีวการแพทย์ (Research in B...  0.000000
41     การวิจัยแบบผสมผสานทางสุขภาพ (Mixed Methods Res...  0.011404
42     การวินิจฉัยภาวะฉุกเฉินจากอุบัติเหตุ (Diagnosti...  0.277145
43     การวินิจฉัยภาวะฉุกเฉินที่ไม่ได้เกิดจากอุบัติเห...  0.244758
44     การวิเคราะห์ข้อมูลการวิจัยทางพฤติกรรมศาสตร์และ...  0.000000
45     การวิเคราะห์ข้อมูลขนาดใหญ่ทางสาธารณสุข (Big Da...  0.000000
46     การวิเคราะห์ข้อมูลอัจฉริยะด้วย RapidMiner (Int...  0.000000
47     การวิเคราะห์ผลตอบแทนทางสังคมในงานด้านสุขภาพ (S...  0.000000
48     การสร้าง AI ขั้นพื้นฐานด้วย RapidMiner และ Exc...  0.000000
49     การสอบวัดผลการเรียนรู้ระดับมัธยมปลาย (ม.6) สำห...  0.000000
50         การออกแบบกิจกรรมผ่านจิตวิทยาเชิงบวก รุ่นที่ 1  0.000000
51         การออกแบบกิจกรรมผ่านจิตวิทยาเชิงบวก รุ่นที่ 2  0.007906
52             การอำนวยเพลงและการสอนวงขับร้องประสานเสียง  0.000000
53     การเขียนแบบวิศวกรรม (Engineering Drawing) - สำ...  0.000000
54     การเขียนแบบวิศวกรรม (Engineering Drawing) 2566...  0.000000
55     การเขียนแบบวิศวกรรม (Engineering Drawing) 2566...  0.002659
56     การเขียนโครงการและกระบวนการใช้จ่ายเงินในกิจกรร...  0.000000
57     การเขียนโครงการและกระบวนการใช้จ่ายเงินในกิจกรร...  0.000000
58     การเขียนโครงการและกระบว

In [59]:
def get_score_of_selected_courses(course_names):
    # Take index of the selected courses
    idx = [ process.extractOne(course_name, courses)[2] for course_name in course_names ]
    
    # take the selected course
    course_scores = []
    for course in courses:
        if course not in course_names:
            course_scores.append(recommender_knn_all_courses(course).iloc[idx])
            
    course_score_dict = {}
    for i,name in enumerate(course_names):
        course_score_dict[name] = []
        for score in course_scores:
            course_score_dict[name].append(score['Score'].iloc[i])
           
    course_score_df = pd.DataFrame(course_score_dict, index=range(0,len(course_scores)))
    
    return course_score_df.max()

In [60]:
def recommender_knn_by_user(user_name, n_recommendations):
    df = {
        'User': pd.Series(file['ชื่อ-นามสกุล (อังกฤษ)']),
        'Course': pd.Series(file['หลักสูตรอบรมระยะสั้น'])
    }
    
    user_course = pd.DataFrame(df)
    selected_user_name = user_course.loc[user_course['User'] == user_name]
    selected_courses = selected_user_name['Course']
    
    recommended_courses = [ recommender_knn_all_courses(x) for x in selected_courses]
    
    # pre dataframe
    df = pd.DataFrame({
        'Course': [],
        'Score': []
    }).rename_axis('Index')
    
    for x in recommended_courses:
        df = df._append(x)
    df =  df.sort_values('Score', ascending=False).drop_duplicates('Course')
    return df.head(n_recommendations)

Items show permanence whereas, people change with time
Items are fewer in numbers to deal with. Which leads to smaller similarity matrix. Amazon and Netflix use it!
Better for New users:
— Him selecting just one item will let us provide recommendations
— But for user based, new user has to wait until next build of similarity matrix (which is the only computational part of the framework)

In [61]:
recommender_knn_by_user('THANAKORN DARASRISAK', 10)

Course     Score
Index                                                             
43     การวินิจฉัยภาวะฉุกเฉินที่ไม่ได้เกิดจากอุบัติเห...  0.752832
131    หลักการและพื้นฐานของเครื่องมือทางรังสีวิทยา (B...  0.277145
110                                   รังสีวิทยาวินิจฉัย  0.225533
152    เตรียมความพร้อมทางรังสีวิทยาสำหรับบุคลากรทางกา...  0.174601
124    สารสนเทศทางสาธารณสุข 2566 (Public Health Infor...  0.071270
41     การวิจัยแบบผสมผสานทางสุขภาพ (Mixed Methods Res...  0.031794
117    วิทยาศาสตร์การแพทย์คลินิก สาขาวิชาเวชศาสตร์ฉุก...  0.023493
136    หลักสูตรอบรมเข้มข้นระยะสั้นแพทย์-วิศวกรรมและวิ...  0.021809
98                                 ทักษะความเป็นนักดนตรี  0.016790
123    สอบคัดเลือกเพื่อเข้าอบรมหลักสูตรอบรมเข้มข้นระย...  0.014994

Training and Testing

In [62]:
from sklearn.model_selection import train_test_split
from sklearn.neighbors import KNeighborsRegressor

Predata of training

In [63]:
# Take 2 columns from Table
course_score = df[['Course', 'Score']]

# Sort the course
course = df['Course'].sort_values().unique()

# Calculate the mean of each course
course_mean = course_score.groupby('Course')
course_mean = course_mean.mean().loc[:, 'Score']

# Take 2 columns from Table
course_user = df[['Course', 'User']]

# Count the number of users who enrolled each course 
course_count = course_user.value_counts('Course')
course_count = course_count.sort_index()

# Take feature columns from Table
course_feature = df[['Course', 'Email Score', 'Age Education Score', 'Enrollment', 'Payment Score', 'Address Score']]
agg_functions = {
    'Email Score': 'mean',
    'Age Education Score': 'mean',
    'Enrollment': 'mean',
    'Payment Score': 'mean',
    'Address Score': 'mean',
}
course_feature = course_feature.groupby('Course').aggregate(agg_functions)
course_feature

Email Score  \
Course                                                            
Cancer Epidemiology and Prevention                     1.000000   
Coaching Skill : Crafting a New You สำหรับนักศึ...     1.714286   
Coaching Skill : Crafting a New You สำหรับบุคลา...     1.692308   
Development Studies & Social Research Specializ...     1.028571   
Digital Transformation: e-Document                     1.863636   
Environmental Economics (USAC programs) - Fall ...     1.000000   
Global Citizenship – โรงเรียนมงฟอร์ตวิทยาลัย สำ...     1.000000   
Global Citizenship – โรงเรียนมงฟอร์ตวิทยาลัย สำ...     1.000000   
Global Citizenship – โรงเรียนสันป่าตองวิทยาคม 2566     1.000000   
Global Citizenship – โรงเรียนแม่ริมวิทยาคม 2566        1.000000   
Global Politics – โรงเรียนปรินส์รอยแยลส์วิทยาลั...     1.000000   
Global Politics – โรงเรียนสันป่าตองวิทยาคม 2566        1.000000   
Global Politics – โรงเรียนแม่ริมวิทยาคม 2566           1.000000   
Mindfulness for Life and Learning : สติเพื่อชีว...     1.777778   
Mindfulness for Life and Work : สติเพื่อชีวิตแล...     1.606061   
Modern Chinese History (USAC program) – Spring ...     1.000000   
Political Science and Public Administration for...     1.000000   
Political Science and Public Administration for...     1.000000   
Sociology and Anthropology of Northern Thailand...     1.000000   
Sociology and Anthropology of Northern Thailand...     1.000000   
Sustainable Agriculture Development (USAC progr...     1.000000   
Sustainable Agriculture Development (USAC progr...     1.000000   
Thai Cultural Education for International Stude...     1.000000   
Thai Cultural Education for International Stude...     1.000000   
Thai Cultural Education for International Stude...     1.000000   
Thai Cultural Education for International Stude...     1.000000   
World Economic Issues (USAC program) – Spring S...     1.000000   
World Economic Issues (USAC program) – Summer 2...     1.000000   
กฎหมายกีฬาเบื้องต้น (Introduction to Sports Law)       1.142857   
การขับร้องประสานเสียงขั้นพื้นฐาน                       1.450000   
การชันสูตรศพและการสอนการชันสูตรศพตามกฎหมาย (Dip...     1.000000   
การดูแลสุขภาพสำหรับสัตว์เลี้ยง (Health Care of ...     1.028846   
การตรวจวิเคราะห์พื้นฐานทางพิษวิทยาและการตรวจวิเ...     1.000000   
การบริบาลทางเภสัชกรรม สาขาผู้ป่วยมะเร็ง (ปี 256...     1.000000   
การบริบาลทางเภสัชกรรม สาขาอายุรศาสตร์ (ปี 2567)...     1.000000   
การบริบาลทางเภสัชกรรมในผู้ป่วยโรคหัวใจและหลอดเล...     1.000000   
การบริบาลทางเภสัชกรรมในผู้ป่วยโรคหัวใจและหลอดเล...     1.000000   
การป้องกันการล้มสำหรับผู้สูงอายุ                       2.000000   
การฝึกอบรมเนื้อหาดิจิทัล (Digital Content) ประจ...     1.300971   
การพัฒนาปัญญาด้วยเกมต่อศัพท์ภาษาอังกฤษ (Intelle...     1.125000   
การวิจัยด้านวิศวกรรมชีวการแพทย์ (Research in Bi...     1.000000   
การวิจัยแบบผสมผสานทางสุขภาพ (Mixed Methods Rese...     1.000000   
การวินิจฉัยภาวะฉุกเฉินจากอุบัติเหตุ (Diagnostic...     1.122302   
การวินิจฉัยภาวะฉุกเฉินที่ไม่ได้เกิดจากอุบัติเหต...     1.113636   
การวิเคราะห์ข้อมูลการวิจัยทางพฤติกรรมศาสตร์และส...     1.571429   
การวิเคราะห์ข้อมูลขนาดใหญ่ทางสาธารณสุข (Big Dat...     1.000000   
การวิเคราะห์ข้อมูลอัจฉริยะด้วย RapidMiner (Inte...     1.000000   
การวิเคราะห์ผลตอบแทนทางสังคมในงานด้านสุขภาพ (So...     1.312500   
การสร้าง AI ขั้นพื้นฐานด้วย RapidMiner และ Exce...     1.153846   
การสอบวัดผลการเรียนรู้ระดับมัธยมปลาย (ม.6) สำหร...     1.012500   
การออกแบบกิจกรรมผ่านจิตวิทยาเชิงบวก รุ่นที่ 1          1.676471   
การออกแบบกิจกรรมผ่านจิตวิทยาเชิงบวก รุ่นที่ 2          1.703704   
การอำนวยเพลงและการสอนวงขับร้องประสานเสียง              1.400000   
การเขียนแบบวิศวกรรม (Engineering Drawing) - สำห...     1.000000   
การเขียนแบบวิศวกรรม (Engineering Drawing) 2566 ...     1.000000   
การเขียนแบบวิศวกรรม (Engineering Drawing) 2566 ...     1.000000   
การเขียนโครงการและกระบวนการใช้จ่ายเงินในกิจกรรม...     1.884615   
การเขียนโครงการและกระบวนการใช้จ่ายเงินในกิจกรรม...     1.857143   
การเขียนโครงการและกระบวนการใช้จ่

Create the train dataframe

In [64]:
course_feature['Count'] = course_count
course_feature['Score'] = course_mean
train_df = pd.DataFrame(course_feature)
train_df.head(10)

Email Score  \
Course                                                            
Cancer Epidemiology and Prevention                     1.000000   
Coaching Skill : Crafting a New You สำหรับนักศึ...     1.714286   
Coaching Skill : Crafting a New You สำหรับบุคลา...     1.692308   
Development Studies & Social Research Specializ...     1.028571   
Digital Transformation: e-Document                     1.863636   
Environmental Economics (USAC programs) - Fall ...     1.000000   
Global Citizenship – โรงเรียนมงฟอร์ตวิทยาลัย สำ...     1.000000   
Global Citizenship – โรงเรียนมงฟอร์ตวิทยาลัย สำ...     1.000000   
Global Citizenship – โรงเรียนสันป่าตองวิทยาคม 2566     1.000000   
Global Citizenship – โรงเรียนแม่ริมวิทยาคม 2566        1.000000   

                                                    Age Education Score  \
Course                                                                    
Cancer Epidemiology and Prevention                             1.500000   
Coaching Skill : Crafting a New You สำหรับนักศึ...             0.285714   
Coaching Skill : Crafting a New You สำหรับบุคลา...             1.410256   
Development Studies & Social Research Specializ...             0.914286   
Digital Transformation: e-Document                             1.818182   
Environmental Economics (USAC programs) - Fall ...             0.000000   
Global Citizenship – โรงเรียนมงฟอร์ตวิทยาลัย สำ...             0.000000   
Global Citizenship – โรงเรียนมงฟอร์ตวิทยาลัย สำ...             0.000000   
Global Citizenship – โรงเรียนสันป่าตองวิทยาคม 2566             0.000000   
Global Citizenship – โรงเรียนแม่ริมวิทยาคม 2566                0.000000   

                                                    Enrollment  Payment Score  \
Course                                                                          
Cancer Epidemiology and Prevention                    0.500000       2.000000   
Coaching Skill : Crafting a New You สำหรับนักศึ...    0.107143       2.000000   
Coaching Skill : Crafting a New You สำหรับบุคลา...    0.307692       1.589744   
Development Studies & Social Research Specializ...    0.200000       1.628571   
Digital Transformation: e-Document                    0.681818       2.000000   
Environmental Economics (USAC programs) - Fall ...    0.000000       2.000000   
Global Citizenship – โรงเรียนมงฟอร์ตวิทยาลัย สำ...    0.588235       2.000000   
Global Citizenship – โรงเรียนมงฟอร์ตวิทยาลัย สำ...    0.684211       2.000000   
Global Citizenship – โรงเรียนสันป่าตองวิทยาคม 2566    0.500000       0.000000   
Global Citizenship – โรงเรียนแม่ริมวิทยาคม 2566       0.428571       0.000000   

                                                    Address Score  Count  \
Course                                                                     
Cancer Epidemiology and Prevention                       0.000000      2   
Coaching Skill : Crafting a New You สำหรับนักศึ...       1.000000     28   
Coaching Skill : Crafting a New You สำหรับบุคลา...       0.923077     39   
Development Studies & Social Research Specializ...       0.200000     35   
Digital Transformation: e-Document                       0.272727     22   
Environmental Economics (USAC programs) - Fall ...       0.000000      4   
Global Citizenship – โรงเรียนมงฟอร์ตวิทยาลัย สำ...       0.235294     17   
Global Citizenship – โรงเรียนมงฟอร์ตวิทยาลัย สำ...       0.210526     19   
Global Citizenship – โรงเรียนสันป่าตองวิทยาคม 2566       0.025000     40   
Global Citizenship – โรงเรียนแม่ริมวิทยาคม 2566          0.000000      7   

                                                       Score  
Course                                                        
Cancer Epidemiology and Prevention                  4.375000  
Coaching Skill : Crafting a New You สำหรับนักศึ...  4.660714  
Coaching Skill : Crafting a New You สำหรับบุคลา...  4.596154  
Development Studies & Social Research Specializ...  3.778571  
Digital Transformation: e-Document                  5.261364  
Environmental Econo

Split the train and the test

In [35]:
# Get X and y features variables
X = train_df[['Email Score', 'Age Education Score', 'Enrollment', 'Payment Score', 'Address Score', 'Count']]
y = train_df['Score']

# Use the train test split function
X_train, X_test, y_train, y_test = train_test_split(
    X, y, random_state=10, test_size=0.25
)

In [36]:
regressor = KNeighborsRegressor(n_neighbors=3)
regressor.fit(X_train, y_train)
predictions = regressor.predict(X_test)
y_train

Course
การฝึกอบรมเนื้อหาดิจิทัล (Digital Content) ประจำปี 2566                                          0.213592
การวิเคราะห์ผลตอบแทนทางสังคมในงานด้านสุขภาพ (Social Return on Investment (SROI) in Health)       0.362500
วิธีวิทยาการวิจัยทางการศึกษา (Research Methodology in Education) 2566                            0.204762
คลินิกผ่าตัดเล็กในช่องปาก (Minor Oral Surgery Clinic)                                            0.333333
หลักสูตรย่อยที่ 2 การดูแลสุขภาพทั่วไปในสัตว์เลี้ยง (General Health Care of Pet Animal) รุ่น 2    0.266667
                                                                                                   ...   
วิทยาศาสตร์การแพทย์คลินิก สาขาวิชากุมารเวชศาสตร์                                                 0.281481
การเขียนโครงการและกระบวนการใช้จ่ายเงินในกิจกรรมนักศึกษา รุ่นที่ 5                                0.276190
Modern Chinese History (USAC program) – Spring semester 2023                                     0.266667
สิทธิและหน้าที่ของผู้แทนนักศึกษามหาวิทย

In [37]:
print("Mean Squared Error:", mean_squared_error(predictions,y_test))
print("Mean Absolute Error:", mean_absolute_error(predictions,y_test))

Mean Squared Error: 0.004050789561947059
Mean Absolute Error: 0.04802461505919834
